# Lab 2: Ingesta de datos con Logstash

En esta práctica vamos a parender a configurar el servicio de Logstash para ingestar datos en eleastic serch:
* Configurar Logstash para leer los ficheros de una carpeta 
* Parsear un fichero de logs con datos semiestructurados.
* Configurar Logstash para escribir los datos procesados en Elasticsarch.

La practica consiste en leer los ficheros de log que genera un supuesto servidor web, procesarlos de forma automática, parsear la información y enriquecerla y por último insertarla en Elasticsearch.

Antes de nada vamos a ver que formato tienen los datos:

In [3]:
import pandas as pd

log_lines = open("../../data/elasticsearch/web_logs/web.log", "r")

for line in log_lines:
    print(line)


66.249.66.194 - - [22/Jan/2019:03:57:54 +0330] "GET /m/filter/b1,p6 HTTP/1.1" 200 19486 "-" "Mozilla/5.0 (Linux; Android 6.0.1; Nexus 5X Build/MMB29P) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/41.0.2272.96 Mobile Safari/537.36 (compatible; Googlebot/2.1; +http://www.google.com/bot.html)" "-"

89.47.79.75 - - [22/Jan/2019:03:59:11 +0330] "GET /static/images/search-category-arrow.png HTTP/1.1" 200 217 "https://znbl.ir/static/bundle-bundle_site_head.css" "Mozilla/5.0 (Windows NT 6.3; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/71.0.3578.98 Safari/537.36" "-"

54.36.148.161 - - [22/Jan/2019:04:00:52 +0330] "GET /filter/b2%2Cb35%2Cb36%2Cp6?o=v39 HTTP/1.1" 302 0 "-" "Mozilla/5.0 (compatible; AhrefsBot/6.1; +http://ahrefs.com/robot/)" "-"

130.185.74.243 - - [22/Jan/2019:04:03:24 +0330] "GET /image/27352/productModel/150x150 HTTP/1.1" 200 2999 "-" "Mozilla/5.0 (Windows NT 6.1; rv:42.0) Gecko/20100101 Firefox/42.0" "-"

66.249.66.91 - - [22/Jan/2019:04:05:56 +0330] "GET /filt

162.158.64.74 - - [22/Jan/2019:09:53:33 +0330] "GET /m/browse/Tad-Lai-Lai/%D9%86%DB%8C-%D9%86%DB%8C-%D9%84%D8%A7%DB%8C-%D9%84%D8%A7%DB%8C HTTP/1.1" 200 18240 "-" "Mozilla/5.0 (Linux; Android 6.0.1; Nexus 5X Build/MMB29P) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/41.0.2272.96 Mobile Safari/537.36 (compatible; Cloudflare-AMPHTML)" "-"

5.218.251.63 - - [22/Jan/2019:09:54:03 +0330] "GET /image/58346/productModel/200x200 HTTP/1.1" 200 0 "https://www.zanbil.ir/m/browse/washing-machine/%D9%85%D8%A7%D8%B4%DB%8C%D9%86-%D9%84%D8%A8%D8%A7%D8%B3%D8%B4%D9%88%DB%8C%DB%8C" "Mozilla/5.0 (iPhone; CPU iPhone OS 11_4_1 like Mac OS X) AppleWebKit/605.1.15 (KHTML, like Gecko) Version/11.0 Mobile/15E148 Safari/604.1" "-"

162.158.64.210 - - [22/Jan/2019:09:54:16 +0330] "GET /browse/juicer-blender/%D8%A2%D8%A8%D9%85%DB%8C%D9%88%D9%87-%DA%AF%DB%8C%D8%B1%DB%8C-%D9%88-%D9%85%D8%AE%D9%84%D9%88%D8%B7-%DA%A9%D9%86 HTTP/1.1" 200 29625 "http://www.zanbil.ir/browse/juicer-blender/%D8%A2%D8%A8%D9%85%DB%8C%D9%88%D

5.202.237.175 - - [22/Jan/2019:10:55:07 +0330] "GET /static/images/arrow-left.png HTTP/1.1" 200 474 "https://znbl.ir/static/bundle-bundle_site_head.css" "Mozilla/5.0 (Windows NT 6.1; rv:64.0) Gecko/20100101 Firefox/64.0" "-"

5.210.207.0 - - [22/Jan/2019:10:55:16 +0330] "GET /static/images/amp/third-party/footer-mobile.png HTTP/1.1" 200 62894 "https://www.zanbil.ir/m/search/%D8%A8%D8%AE%D8%A7%D8%B1%D9%8A-%DA%AF%D8%A7%D8%B2%D9%8A-%D9%86%D9%8A%D9%83-%D9%83%D8%A7%D9%84%D8%A7" "Mozilla/5.0 (iPhone; CPU iPhone OS 10_2_1 like Mac OS X) AppleWebKit/602.4.6 (KHTML, like Gecko) Version/10.0 Mobile/14D27 Safari/602.1" "-"

151.243.236.99 - - [22/Jan/2019:10:55:24 +0330] "GET /image/65271/productModel/150x150 HTTP/1.1" 200 3181 "https://www.zanbil.ir/browse/cell-phone/%DA%AF%D9%88%D8%B4%DB%8C-%D9%85%D9%88%D8%A8%D8%A7%DB%8C%D9%84" "Mozilla/5.0 (Windows NT 6.1; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/71.0.3578.98 Safari/537.36" "-"

77.104.75.68 - - [22/Jan/2019:10:55:36 +0330] "G

5.190.92.12 - - [22/Jan/2019:13:27:32 +0330] "GET /image/53287/productModel/100x100 HTTP/1.1" 200 2451 "https://www.zanbil.ir/browse/printer/%D9%BE%D8%B1%DB%8C%D9%86%D8%AA%D8%B1" "Mozilla/5.0 (Windows NT 6.1; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/71.0.3578.98 Safari/537.36" "-"

217.218.220.252 - - [22/Jan/2019:13:27:43 +0330] "GET /image/1546/productModel/150x150 HTTP/1.1" 200 3137 "https://www.zanbil.ir/filter/b1,b2,p47" "Mozilla/5.0 (Windows NT 6.1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/71.0.3578.98 Safari/537.36" "-"

5.52.72.94 - - [22/Jan/2019:13:27:49 +0330] "GET /image/45/brand HTTP/1.1" 200 2628 "https://www.zanbil.ir/browse/home-appliances/%D9%84%D9%88%D8%A7%D8%B2%D9%85-%D8%AE%D8%A7%D9%86%DA%AF%DB%8C" "Mozilla/5.0 (Windows NT 6.1; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/71.0.3578.98 Safari/537.36" "-"

188.136.224.15 - - [22/Jan/2019:13:27:59 +0330] "GET /filter/b2%2Cp65%2C6313%7C49%20%D8%A7%DB%8C%D9%86%DA%86?o=6313 HTTP/1.1" 302 

192.15.237.81 - - [22/Jan/2019:13:59:10 +0330] "GET /image/46404/productModel/200x200 HTTP/1.1" 200 4293 "https://www.zanbil.ir/m/filter/p2598%2Ct450?name=%D8%B3%DB%8C%D9%86%DA%A9-%D8%B8%D8%B1%D9%81%D8%B4%D9%88%DB%8C%DB%8C&productType=kitchen-sink" "Mozilla/5.0 (Linux; Android 6.0.1; SM-C5000) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/70.0.3538.80 Mobile Safari/537.36" "-"

91.99.30.32 - - [22/Jan/2019:13:59:21 +0330] "GET /rapidGrails/jsonList?maxColumns=16&domainClass=eshop.Order&filter=[{op:%27inSession%27,%20field:%27id%27,%20val:%27orderList04bfc5f7823b405aa70dacc9aea70065%27}]&columns=[{%27name%27:%27trackingCode%27,%27width%27:110},{%27name%27:%27ownerName%27,%27width%27:120},{%27name%27:%27productsName%27,%27width%27:320,%27sortable%27:false},{%27name%27:%27ownerMobile%27,%27width%27:110},{%27name%27:%27deliveryMethodName%27,%27width%27:120,%27sortable%27:false},{%27name%27:%27deliveryCityName%27,%27width%27:120,%27sortable%27:false},{%27name%27:%27addressRegionName%27,%27w

...

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




2.186.230.209 - - [26/Jan/2019:09:30:45 +0330] "GET /image/56742/productModel/150x150 HTTP/1.1" 200 2696 "https://www.zanbil.ir/search/%D9%87%D9%88%D8%AF/p0?s=" "Mozilla/5.0 (Windows NT 5.1; rv:52.0) Gecko/20100101 Firefox/52.0" "-"

77.237.69.185 - - [26/Jan/2019:09:30:58 +0330] "GET /image/56796/productModel/100x100 HTTP/1.1" 200 1405 "https://www.zanbil.ir/filter/b148,p2597" "Mozilla/5.0 (Windows NT 6.1; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/71.0.3578.98 Safari/537.36" "-"

94.183.158.227 - - [26/Jan/2019:09:31:08 +0330] "GET /static/images/arrow-right.png HTTP/1.1" 200 475 "https://znbl.ir/static/bundle-bundle_site_head.css" "Mozilla/5.0 (Windows NT 6.1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/71.0.3578.98 Safari/537.36" "-"

77.237.69.185 - - [26/Jan/2019:09:32:00 +0330] "POST /ajaxFilter/b148,p2597?page=1 HTTP/1.1" 200 4561 "https://www.zanbil.ir/filter/b148,p2597" "Mozilla/5.0 (Windows NT 6.1; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/7

94.183.71.77 - - [26/Jan/2019:11:31:18 +0330] "GET /static/images/icons/btn-search.png HTTP/1.1" 200 393 "https://znbl.ir/static/bundle-bundle_site_head.css" "Mozilla/5.0 (Windows NT 6.1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/71.0.3578.98 Safari/537.36" "-"

2.187.212.147 - - [26/Jan/2019:11:31:28 +0330] "GET /image/29968/productModel/100x100 HTTP/1.1" 200 1847 "https://www.zanbil.ir/product/5945/%D9%81%D8%B4%D8%A7%D8%B1%D8%B3%D9%86%D8%AC-%D8%A8%D8%A7%D8%B2%D9%88%DB%8C%DB%8C-%D8%A8%DB%8C%D9%88%D8%B1%D8%B1-%D9%85%D8%AF%D9%84-Upper-arm-Blood-Pressure-Monitor-BM16" "Mozilla/5.0 (Windows NT 6.1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/71.0.3578.98 Safari/537.36" "-"

5.114.87.113 - - [26/Jan/2019:11:31:41 +0330] "GET /amp-helper-frame.html?appId=a624a1c1-0c93-466a-a546-e146710f97e6&parentOrigin=https://www-zanbil-ir.cdn.ampproject.org HTTP/1.1" 200 133 "https://www-zanbil-ir.cdn.ampproject.org/v/s/www.zanbil.ir/m/browse/refrigerator-and-freezer/%DB%8C%D8%AE%DA%86%D8%A7%D9%84-


2.181.89.103 - - [26/Jan/2019:14:16:08 +0330] "GET /image/62326/productModel/150x150 HTTP/1.1" 200 3147 "https://www.zanbil.ir/filter/b2,p6" "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/69.0.3497.100 Safari/537.36" "-"

195.181.60.97 - - [26/Jan/2019:14:16:14 +0330] "GET /image/34899/productModel/100x100 HTTP/1.1" 200 1418 "https://www.zanbil.ir/product/17771/34873/%DA%A9%D9%88%D9%84%D8%B1-%DA%AF%D8%A7%D8%B2%DB%8C-%D8%A7%D8%B3%D9%BE%D9%84%DB%8C%D8%AA-%D9%87%D8%A7%DB%8C%D8%B3%D9%86%D8%B3-%D9%85%D8%AF%D9%84-HRH-12TQ" "Mozilla/5.0 (Windows NT 6.1; Win64; x64; rv:64.0) Gecko/20100101 Firefox/64.0" "-"

151.239.241.163 - - [26/Jan/2019:14:16:18 +0330] "GET /rapidGrails/jsonList?maxColumns=16&domainClass=eshop.Order&columns=[{%27name%27:%27trackingCode%27,%27width%27:110},{%27name%27:%27ownerName%27,%27width%27:120},{%27name%27:%27productsName%27,%27width%27:320,%27sortable%27:false},{%27name%27:%27ownerMobile%27,%27width%27:110},{%27name%27:%27de

2.179.206.116 - - [26/Jan/2019:17:34:18 +0330] "GET / HTTP/1.1" 302 0 "-" "Mozilla/5.0 (iPhone; CPU iPhone OS 12_1 like Mac OS X) AppleWebKit/605.1.15 (KHTML, like Gecko) CriOS/71.0.3578.89 Mobile/15E148 Safari/605.1" "-"

2.176.224.42 - - [26/Jan/2019:17:34:33 +0330] "GET /image/22401?name=product_95_1429611630_17450.jpg&wh=200x200 HTTP/1.1" 200 5108 "https://torob.com/p/4f9e002b-fa35-48f1-833a-e6f79ebc2359/%D8%AF%DB%8C%D9%88%D8%A7%D9%86-%D8%AD%D8%A7%D9%81%D8%B8-%D8%A7%D9%86%D8%AA%D8%B4%D8%A7%D8%B1%D8%A7%D8%AA-%D9%87%D9%84%DB%8C%D8%A7-%D9%85%D8%AF%D9%84-%D9%88%D8%B2%DB%8C%D8%B1%DB%8C-%D9%82%D8%A7%D8%A8%D8%AF%D8%A7%D8%B1-%D8%B3%D9%84%D9%81%D9%88%D9%86/" "Mozilla/5.0 (Linux; Android 8.1.0; SAMSUNG SM-J730GM Build/M1AJQ) AppleWebKit/537.36 (KHTML, like Gecko) SamsungBrowser/8.2 Chrome/63.0.3239.111 Mobile Safari/537.36" "-"

5.209.159.248 - - [26/Jan/2019:17:34:40 +0330] "GET /filter/p62,stexists HTTP/1.1" 302 0 "https://www.zanbil.ir/m/browse/cell-phone/%DA%AF%D9%88%D8%B4%DB%8C-%D9%85%D

Como podemos ver el fichero no tiene estructura, pero podemos asumir que hay cierta información que se repite en cada línea del log:

* IP que hace la petición
* Fehca en la que se realiza la petición
* Verbo o método HTTP de la petición
* La URL del recurso pedido
* El código de la respuesta
* El User agent del cliente que hizo la petición
* Etc.

Por lo que aunque el fichero no tenga estructura, las lineas del log mantienen un formato que vamos a poder parsear y convertir a un formato estructurado a través de Logstash y de los pipelines de ingesta de Elasticsearch.

Una vez parseada la linea y estructurada en un documento, vamos a insertar estos documentos en Elasticsearch para poderlos consultar y extraer el conocimiento que necesitemos sobre este servicio.

## Paso 1: Creamos un template para los índices que generemos al insertar los documentos

Cuando el volumen de datos que almacenamos es muy grande, es muy común tener varios índies con los documentos que guardamos, de tal forma que podamos aplicar distintas polítcas de gestión de índices en función de la temperatura del dato. Por tanto vamos a crear un índice para cada día de logs.
Cada índice que creemos tendrá el siguiente nombre web-logs-{fecha}.

Para crear cada índice de forma dinámica y asignarle el mapping type adecuado sin tener que hacerlo de forma manual, vamos a crear un template para todos los índices cuyo nombre cumplan en patrón web-logs-*

El mapping que vamos a crear está basado en el Mapping Common Schema (ECS por sus siglas en inglés). ECS es un mapping open source creado por Elastic a partir de las necesidades de la comunidad para almacenar datos provenientes de logs y métricas de diferentes servicios y aplicaciones con el objetivo de tener un esquema estandard para poder sonstrurir sobre él cualquier casos de uso.

Entre los beneficios de ECS encontramos:
* Simplicidad para relacionar datos de distintas fuentes.
* Facilidad de recordar el nombre de campos comunes aun gestionando multitud de fuentes, ya que se mantienen en todas ellas igual.
* Posibilidad de reutilizar contenido de análisis previos, tanto visualizaciones y dashboards, como el resto de contenido, ya sean búsquedas, alarmas, reportes o trabajos de Machine Learning existentes.

Para más informcación sobre ECS puedes consultar su página de documentación: https://www.elastic.co/guide/en/ecs/current/index.html

Para este ejemplo y con el objetivo de poder manejar de forma mas sencilla el mapping desde un notebook nos vamos a quedar únicamente con los campos necesarios para almacenar infromación de un access log de Apache.


`
PUT /_index_template/web-logs
{
  "index_patterns": ["web-logs"],
  "template": {
    "mappings": {
      "dynamic_templates": [
        {
          "strings_as_keyword": {
            "mapping": {
              "ignore_above": 1024,
              "type": "keyword"
            },
            "match_mapping_type": "string"
          }
        }
      ],
      "date_detection": false,
      "properties": {        
        "log": {
          "properties": {
            "file": {
              "properties": {
                "path": {
                  "ignore_above": 1024,
                  "type": "keyword"
                }
              }
            }
          }
        },
        "source": {
          "properties": {
            "address": {
              "ignore_above": 1024,
              "type": "keyword"
            },
            "ip": {
              "type": "ip"
            },
            "geo": {
              "properties": {
                "region_iso_code": {
                  "ignore_above": 1024,
                  "type": "keyword"
                },
                "continent_name": {
                  "ignore_above": 1024,
                  "type": "keyword"
                },
                "city_name": {
                  "ignore_above": 1024,
                  "type": "keyword"
                },
                "country_iso_code": {
                  "ignore_above": 1024,
                  "type": "keyword"
                },
                "name": {
                  "ignore_above": 1024,
                  "type": "keyword"
                },
                "country_name": {
                  "ignore_above": 1024,
                  "type": "keyword"
                },
                "region_name": {
                  "ignore_above": 1024,
                  "type": "keyword"
                },
                "location": {
                  "type": "geo_point"
                }
              }
            },
            "as": {
              "properties": {
                "number": {
                  "type": "long"
                },
                "organization": {
                  "properties": {
                    "name": {
                      "ignore_above": 1024,
                      "fields": {
                        "text": {
                          "norms": false,
                          "type": "text"
                        }
                      },
                      "type": "keyword"
                    }
                  }
                }
              }
            }
          }
        },
        "url": {
          "properties": {
            "original": {
              "ignore_above": 1024,
              "type": "keyword",
              "fields": {
                "text": {
                  "norms": false,
                  "type": "text"
                }
              }
            }
          }
        },
        "apache": {
          "properties": {
            "access": {
              "properties": {
                "ssl": {
                  "properties": {
                    "cipher": {
                      "ignore_above": 1024,
                      "type": "keyword"
                    },
                    "protocol": {
                      "ignore_above": 1024,
                      "type": "keyword"
                    }
                  }
                }
              }
            },
            "error": {
              "properties": {
                "module": {
                  "ignore_above": 1024,
                  "type": "keyword"
                }
              }
            }
          }
        },
        "@timestamp": {
          "type": "date"
        },
        "http": {
          "properties": {
            "request": {
              "properties": {
                "referrer": {
                  "ignore_above": 1024,
                  "type": "keyword"
                },
                "method": {
                  "ignore_above": 1024,
                  "type": "keyword"
                }
              }
            },
            "response": {
              "properties": {
                "status_code": {
                  "type": "long"
                },
                "body": {
                  "properties": {
                    "bytes": {
                      "type": "long"
                    }
                  }
                }
              }
            },
            "version": {
              "ignore_above": 1024,
              "type": "keyword"
            }
          }
        },   
        "event": {
          "properties": {
            "ingested": {
              "type": "date"
            },
            "outcome": {
              "ignore_above": 1024,
              "type": "keyword"
            },
            "original": {
              "type": "text"
            },
            "created": {
              "type": "date"
            },
            "kind": {
              "ignore_above": 1024,
              "type": "keyword"
            },
            "category": {
              "ignore_above": 1024,
              "type": "keyword"
            }
          }
        },
        "user": {
          "properties": {
            "name": {
              "ignore_above": 1024,
              "type": "keyword",
              "fields": {
                "text": {
                  "norms": false,
                  "type": "text"
                }
              }
            }
          }
        },
        "user_agent": {
          "properties": {
            "original": {
              "ignore_above": 1024,
              "type": "keyword",
              "fields": {
                "text": {
                  "norms": false,
                  "type": "text"
                }
              }
            },
            "os": {
              "properties": {
                "name": {
                  "ignore_above": 1024,
                  "type": "keyword",
                  "fields": {
                    "text": {
                      "norms": false,
                      "type": "text"
                    }
                  }
                },
                "version": {
                  "ignore_above": 1024,
                  "type": "keyword"
                },
                "full": {
                  "ignore_above": 1024,
                  "type": "keyword",
                  "fields": {
                    "text": {
                      "norms": false,
                      "type": "text"
                    }
                  }
                }
              }
            },
            "name": {
              "ignore_above": 1024,
              "type": "keyword"
            },
            "version": {
              "ignore_above": 1024,
              "type": "keyword"
            },
            "device": {
              "properties": {
                "name": {
                  "ignore_above": 1024,
                  "type": "keyword"
                }
              }
            }
          }
        }
      }
    }
  }
}
`

1. Para comprobar que se ha creado correctamente entra en la sección Index Templates de Kibana y busca el template que vamos a crear "web_logs"


* Kibana > menú > Management > Stack Management > Data > Index Management > pestaña Index Templates.

## Paso 2: Creamos un pipeline para procesar los datos

Para procesar los datos que lleguen de Logstash, parsearlos, estructurarlos y enriquecerlos vamos a crear un pipeline de ingesta como vimos en la práctica anterior.

Todos los processors se entienden con los ejemplos que vimos anteriormente, pero vamos a centrarnos en el processor grok que es más complicado de entender y es realmente donde hacemos toda la "magia" de parseo y enriquecimeinto de los datos.

El processor grok recibe este nombre del lenguaje que vamos a utilizar para parsear las cadenas de texto de los logs. Este lenguaje se basa en aplicar expresiones regulares sobre cadenas de texto para buscar patrones que se repiten en los datos y que hacen referencia a cierta información. Por ejemplo la expresión %{IP:client} es capáz de aplicar la expresión regular que representa a una IP y asignarselo al campo client del documento que estamos generando.

Grok ha evolucionado bastante y ya tiene predefinidas las expresiones regulares de la mañoría de patrones que buscamos nomalmente en una cadena de log.

Para ver como funciona vamos a utilizar una de las Dev Tools de Kibana, Grok Debugger, que nos permite crear y depurar nuestro script de gork.

Primero entremos en el Grok Debugger:

* Kibana > menú > Dev Tools > pestaña Grok Debugger

Vamos a coger una línea del fichero de logs que queremos parsear y la vamos a utilizar como cadena de ejemplo sobre la que aplicar el script que vayamos generando.

`
89.47.79.75 - - [22/Jan/2019:03:59:11 +0330] "GET /static/images/search-category-arrow.png HTTP/1.1" 200 217 "https://znbl.ir/static/bundle-bundle_site_head.css" "Mozilla/5.0 (Windows NT 6.3; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/71.0.3578.98 Safari/537.36" "-"
`

Y vamos a ir aplicando diferentes expresiones para ver como parsear y extraer toda la información que podamos de la linea del log.

Por ejemplo, lo primero que reconocemos en esta es la dirección IP del cliente que realiza la petción, si introduccimos el siguieten patrón %{IP:destination} y clickamos en "simulate" veremos que genera un documento con el campo "destination" con valor la IP que figura en la línea de log. 
La expresión regular que está aplicando es la siguiente:
* IP (?:%{IPV6}|%{IPV4})

Puede ser que en la línea de log venga una IP o un Hostname Si nos queremos asegurar que pueda extarer tanto IPs como nombres de dominio, podemos usar el patrón %{IPORHOST:destination.domain}. 

1. Ejecuta el pattern %{IPORHOST:destination.domain} para ver como funciona.

Bien, vamos ahora a intentar extraer la fehca y la hora en la que se realizo la petición que sería el siguiente dato que somos capaces de reconocer. Para ello vamos a utilizar el patrón predefinido HTTPDATE:
* HTTPDATE: %{MONTHDAY}/%{MONTH}/%{YEAR}:%{TIME} %{INT}

`
%{IPORHOST:source.address} - - \[%{HTTPDATE:apache.access.time}\] 
`

1. Ejecuta este patrón en Grok Debugger

Como la fecha viene entre dos corchetes, se lo tenemos que indicar a la expresión y además como son caracteres reservados del lenguaje Grok los tenemos que escapar.

Vamos ahora a extraer la información de la petición, para ello usaremos los siguientes patrones:

* WORD: \b\w+\b
* DATA: .*?
* NUMBER: (?:%{BASE10NUM})

El escript quedaría de la siguiente manera:

`
%{IPORHOST:source.address} - - \[%{HTTPDATE:apache.access.time}\] \"(?:%{WORD:http.request.method} %{DATA:url.original} HTTP/%{NUMBER:http.version}|-)?\"
`

1. Ejecuta este patrón en Grok Debugger

De esta manera seguiríamos parseando y extrayendo información de la cadena de log.

En este enlace tienes un listado con todos los patrones predefinidos por Elastic: https://github.com/elastic/elasticsearch/blob/main/libs/grok/src/main/resources/patterns/legacy/grok-patterns


Otro processor interesante que vamos a utilizar es geoip que nos permite buscar en una base de datos de IPs la dirección que hemos parseado y buscar sus coordenadas geográficas. De esta forma nos sólo estructuramos la información sino que también la aumentamos y enriquecemos con más información relacionada.

Una vez que ya hemos visto como funcionan los processor que vamos a utilizar, creamos el pipeline ejecutando la siguiente sentencia: 

In [1]:
!curl -X PUT http://elasticsearch:9200/_ingest/pipeline/web-logs -H 'Content-Type: application/json' -d ' \
{ \
  "description" : "Pipeline for parsing Apache HTTP Server access logs. Requires the geoip and user_agent plugins.", \
  "processors" : [ \
    { \
      "set": { \
        "field": "event.original", \
        "value": "{{message}}" \
      } \
    }, \
    { \
      "set" : { \
        "field" : "event.ingested", \
        "value" : "{{_ingest.timestamp}}" \
      } \
    }, \
    { \
      "grok" : { \
        "patterns" : [ \
          "%{IPORHOST:destination.domain} %{IPORHOST:source.ip} - %{DATA:user.name} \\[%{HTTPDATE:apache.access.time}\\] \"(?:%{WORD:http.request.method} %{DATA:url.original} HTTP/%{NUMBER:http.version}|-)?\" %{NUMBER:http.response.status_code:long} (?:%{NUMBER:http.response.body.bytes:long}|-)( \"%{DATA:http.request.referrer}\")?( \"%{DATA:user_agent.original}\")?", \
          "%{IPORHOST:source.address} - %{DATA:user.name} \\[%{HTTPDATE:apache.access.time}\\] \"(?:%{WORD:http.request.method} %{DATA:url.original} HTTP/%{NUMBER:http.version}|-)?\" %{NUMBER:http.response.status_code:long} (?:%{NUMBER:http.response.body.bytes:long}|-)( \"%{DATA:http.request.referrer}\")?( \"%{DATA:user_agent.original}\")?", \
          "%{IPORHOST:source.address} - %{DATA:user.name} \\[%{HTTPDATE:apache.access.time}\\] \"-\" %{NUMBER:http.response.status_code:long} -", \
          "\\[%{HTTPDATE:apache.access.time}\\] %{IPORHOST:source.address} %{DATA:apache.access.ssl.protocol} %{DATA:apache.access.ssl.cipher} \"%{WORD:http.request.method} %{DATA:url.original} HTTP/%{NUMBER:http.version}\" (-|%{NUMBER:http.response.body.bytes:long})" \
        ], \
        "ignore_missing" : true, \
        "field" : "message" \
      } \
    }, \
    { \
      "remove" : { \
        "field" : "message" \
      } \
    }, \
    { \
      "set" : { \
        "field" : "event.kind", \
        "value" : "event" \
      } \
    }, \
    { \
      "set" : { \
        "field" : "event.category", \
        "value" : "web" \
      } \
    }, \
    { \
      "set" : { \
        "value" : "success", \
        "if" : "ctx?.http?.response?.status_code != null && ctx.http.response.status_code < 400", \
        "field" : "event.outcome" \
      } \
    }, \
    { \
      "set" : { \
        "field" : "event.outcome", \
        "value" : "failure", \
        "if" : "ctx?.http?.response?.status_code != null && ctx.http.response.status_code > 399" \
      } \
    }, \
    { \
      "grok" : { \
        "field" : "source.address", \
        "ignore_missing" : true, \
        "patterns" : [ \
          "^(%{IP:source.ip}|%{HOSTNAME:source.domain})$" \
        ] \
      } \
    }, \
    { \
      "rename" : { \
        "target_field" : "event.created", \
        "field" : "@timestamp" \
      } \
    }, \
    { \
      "date" : { \
        "ignore_failure" : true, \
        "field" : "apache.access.time", \
        "target_field" : "@timestamp", \
        "formats" : [ \
          "dd/MMM/yyyy:H:m:s Z" \
        ] \
      } \
    }, \
    { \
      "remove" : { \
        "field" : "apache.access.time", \
        "ignore_failure" : true \
      } \
    }, \
    { \
      "user_agent" : { \
        "field" : "user_agent.original", \
        "ignore_failure" : true \
      } \
    }, \
    { \
      "geoip" : { \
        "field" : "source.ip", \
        "target_field" : "source.geo", \
        "ignore_missing" : true \
      } \
    }, \
    { \
      "geoip" : { \
        "target_field" : "source.as", \
        "properties" : [ \
          "asn", \
          "organization_name" \
        ], \
        "ignore_missing" : true, \
        "database_file" : "GeoLite2-ASN.mmdb", \
        "field" : "source.ip" \
      } \
    }, \
    { \
      "rename" : { \
        "field" : "source.as.asn", \
        "target_field" : "source.as.number", \
        "ignore_missing" : true \
      } \
    }, \
    { \
      "rename" : { \
        "ignore_missing" : true, \
        "field" : "source.as.organization_name", \
        "target_field" : "source.as.organization.name" \
      } \
    }, \
    { \
      "set" : { \
        "field" : "tls.cipher", \
        "value" : "{{apache.access.ssl.cipher}}", \
        "ignore_empty_value" : true \
      } \
    }, \
    { \
      "script" : { \
        "lang" : "painless", \
        "if" : "ctx?.apache?.access?.ssl?.protocol != null", \
        "source" : "def parts = ctx.apache.access.ssl.protocol.toLowerCase().splitOnToken(\"v\"); if (parts.length != 2) {\n  return;\n} if (parts[1].contains(\".\")) {\n  ctx.tls.version = parts[1];\n} else {\n  ctx.tls.version = parts[1] + \".0\";\n} ctx.tls.version_protocol = parts[0];" \
      } \
    } \
  ], \
  "on_failure" : [ \
    { \
      "set" : { \
        "field" : "error.message", \
        "value" : "{{ _ingest.on_failure_message }}" \
      } \
    } \
  ] \
}'

{"acknowledged":true}

Comprueba que se ha generado correctamente entrando en la sección de Ingest Pipelines y buscando el pipeline "web-logs" que acabamos de crear:

* Kibana > menú > Management > Stack Management > Ingest > Ingest Pipelines 

## Paso 3: Configuramos Logshtash

Ya sólo nos queda configurar Logshtash para que lea los ficheros de la ruta donde guarda los logs el servidor Apache, indicar los filtros que queremos que aplique y por último decirle en que índice de Elasticsearch queremos que deje los datos.

Por cada instancia o servicio de Logstahs que levantemos podemos ejecutar uno o más pipelines de ingesta. Cada uno de stos procesos se define en su respectivo fichero. Dejaremos estos ficheros en la carpeta pipeline de logstash, en nuestro caso en la ruta '/usr/share/logstash/pipeline/'.

Vamos a definir el pipeline de ingesta para nuestro ejemplo. Lo puedes encontrar aquí: 
http://127.0.0.1:8889/edit/work/data/elasticsearch/web_logs/pipeline/web-logs-logstash.conf


El pipeline tiene tres prates:

* **input** -> indicamos de donde queremos recuparar los dastos que queremos ingestar.

`
input {
    path => "/tmp/data/*"
}
`

Vamos a leer los ficheros de log que se vayan creando el la ruta '/tmp/data/'. 


* **filter** -> definimos la cadena de processors a ejecutar sobre los datos originales para trandformalos y darles estructura.

`
filter {
  mutate {
    remove_field => ["host", "@version"]
  }
}
`

Puesto que hemos creado un pipeline de ingesta, solo le vamos a indicar a Logstash eliminar los campos 'host' y '@version'.


* **output** -> indicamos donde queremos dejar o insertar los datos adquiridos.

`
output {
  stdout {
    codec => dots {}
  }

  elasticsearch {
    hosts => "localhost:9200"
    index => "web-logs"
    pipeline => "web-logs"
  }
}
`

Por un lado vamos a imprmir por panta un punto por cada línea de log parseada. Por otro lado vamos a enviar el documento creado a partir de cada línea de log leída a Elasticsearch. Para ello tenemos que indicar los parámetros de configuración de Elasticsearch, la url o urls de los hosts del cluster de Elasticsearch, el índice donde insertar los docuentos y por último el pipeline a ejecutar a la hora de insertar los datos (este prámetro es opcional).

## Paso 4: Levantar Logstash

En nuestro caso vamos a utilizar una imagen de docker para ejecutar Logstash:

* Para que pueda encontrar el servicio de Elasticsearch vamos a añadir el conteneror a la red de nuestro laboratorio, `--network=datahack-nosql_default`.
* Montamos el volumen donde se encuentra nuestro fichero con el pipeline y los referenciamos a la carpeta del contenedor donde Logstash espera encontrar esa configuración, `-v /Users/rgarrote/desarrollo/datahack-nosql/work/data/elasticsearch/web_logs/pipeline/:/usr/share/logstash/pipeline/`.
* Montamos el volumen donde dejaremos los ficheros de log a parsear. `-v /Users/rgarrote/desarrollo/datahack-nosql/work/data/elasticsearch/web_logs/data/:/tmp/data/`.


In [ ]:
docker run --rm -it --network=curso-els-paradigma_default \
    -v /Users/rgarrote/desarrollo/cursoELS/curso-els-paradigma/work/data/elasticsearch/web_logs/pipeline/:/usr/share/logstash/pipeline/ \
    -v /Users/rgarrote/desarrollo/cursoELS/curso-els-paradigma/work/data/elasticsearch/web_logs/data/:/tmp/data/ \
docker.elastic.co/logstash/logstash:8.3.3

## Paso 5: Comprobar que el proceso se está realizando correctamente

1. Comprueba en Kibana que se ha ceado el íncide web-logs.
2. Desde la sección de Index Management averigua cuantas líneas de log se han insertado en el índice de Elasticsearch.
3. Comprueba que el mapping creado del índice corresponde al del template que hemos creado.
4. Realiza una consulta de con una muestra de 10 documentos para comprobar que los datos se están parseando e insertando correctamente en Elasticsearch.